In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import string
from PIL import Image
from time import time
from keras.preprocessing import sequence
from keras.models import Sequential
from keras.layers import LSTM, Embedding, TimeDistributed, Dense, RepeatVector, Activation, Flatten, Reshape, concatenate, Dropout, BatchNormalization
from keras.optimizers import Adam, RMSprop
from keras.layers.wrappers import Bidirectional
from keras.layers.merge import add
from keras.applications.inception_v3 import InceptionV3
from keras.applications.vgg16 import VGG16
from keras.preprocessing import image
from keras.models import Model
from keras import Input, layers
from keras import optimizers
from keras.applications.inception_v3 import preprocess_input
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
import cv2
import os
import glob
import pickle

Using TensorFlow backend.


In [2]:
filename = "flickr/Flickr8k_text/Flickr8k.token.txt"
file = open(filename, 'r')
doc = file.read()
file.close()
count = 0
for line in doc.split('\n'):
    count = count + 1
print(count)
print(doc[:400])

40461
1000268201_693b08cb0e.jpg#0	A child in a pink dress is climbing up a set of stairs in an entry way .
1000268201_693b08cb0e.jpg#1	A girl going into a wooden building .
1000268201_693b08cb0e.jpg#2	A little girl climbing into a wooden playhouse .
1000268201_693b08cb0e.jpg#3	A little girl climbing the stairs to her playhouse .
1000268201_693b08cb0e.jpg#4	A little girl in a pink dress going into a wood


In [3]:
def load_descriptions(doc):
    mapping = dict()
    for line in doc.split('\n'):
        tokens = line.split()
        if len(line) < 2:
            continue
        image_id = tokens[0]
        image_desc = tokens[1:]
        image_desc = ' '.join(image_desc)
        image_id = image_id.split('.')[0]
        if image_id in mapping:
            mapping[image_id].append(image_desc)
        if image_id not in mapping:
            mapping[image_id] = list()
            mapping[image_id].append(image_desc)
    return mapping
descriptions = load_descriptions(doc)
print('loaded=', len(descriptions))

loaded= 8092


In [4]:
#print(descriptions)
print(list(descriptions.keys())[:5])

['2156131463_5b53636cf0', '2675685200_0913d84d9b', '543264612_c53cc163b4', '3214573346_d3a57f0328', '2436081047_bca044c1d3']


In [5]:
print(len(descriptions))
print(descriptions['1000268201_693b08cb0e'])
print(descriptions['3712923460_1b20ebb131'])

8092
['A child in a pink dress is climbing up a set of stairs in an entry way .', 'A girl going into a wooden building .', 'A little girl climbing into a wooden playhouse .', 'A little girl climbing the stairs to her playhouse .', 'A little girl in a pink dress going into a wooden cabin .']
['a bunch of people in camo pants run .', 'A group of men and woman wearing army pants and a white shirt are running .', 'A group of men in camouflage pants and white t-shirts are running in a drill yard .', 'A group of people in army pants running .', 'A group of people wearing army clothes run together down the street .']


In [6]:
table = str.maketrans('', '', string.punctuation)
for key, desc_list in descriptions.items():
    #print(key, desc_list)
    for i in range(len(desc_list)):
        #print('1',desc_list[i])
        desc = desc_list[i]
        #print('2',desc)
        desc = desc.split()
        #print('3',desc)
        desc = [word.lower() for word in desc]
        #print('4',desc)
        desc = [w.translate(table) for w in desc]
        #print('5',desc)
        desc = [word for word in desc if (len(word) > 1)]
        #print('6',desc)
        desc = [word for word in desc if word.isalpha()]
        #print('7',desc)
        desc_list[i] = ' '.join(desc)
        #print('8',desc_list)
#print(desc_list)
#print(len(descriptions))
print(len(descriptions.keys()))

8092


In [7]:
print(descriptions['3712923460_1b20ebb131'])

['bunch of people in camo pants run', 'group of men and woman wearing army pants and white shirt are running', 'group of men in camouflage pants and white tshirts are running in drill yard', 'group of people in army pants running', 'group of people wearing army clothes run together down the street']


In [8]:
vocabulary = set()
for key in descriptions.keys():
    [vocabulary.update(d.split()) for d in descriptions[key]]
print('size = ', len(vocabulary))
print(len(descriptions))
print(len(descriptions.keys()))

size =  8763
8092
8092


In [9]:
train_captions = []
for key,val in descriptions.items():
    for captions in val:
        train_captions.append(captions)

wordcount_max = 10
word_count = {}
nsents = 0
for sent in train_captions:
    nsents = nsents + 1
    for w in sent.split():
        word_count[w] = word_count.get(w, 0) + 1
vocab = [w for w in word_count if word_count[w] > wordcount_max]
print('words = ', len(vocab))


words =  1839


In [10]:
print(vocab)

['candy', 'line', 'checkered', 'puppies', 'swinging', 'bouncing', 'chain', 'among', 'wheeled', 'tackling', 'asian', 'performs', 'stair', 'crowd', 'creek', 'tulips', 'shower', 'wheeler', 'paper', 'cheek', 'barrier', 'some', 'opens', 'about', 'slope', 'fast', 'buildings', 'racetrack', 'waves', 'obama', 'direction', 'wading', 'tripod', 'cream', 'squirted', 'shows', 'photo', 'been', 'sliding', 'as', 'new', 'brother', 'shaved', 'has', 'nearby', 'mall', 'they', 'bird', 'innertube', 'patch', 'run', 'stuck', 'place', 'surfboard', 'so', 'without', 'chest', 'cut', 'longhaired', 'coffee', 'costume', 'singing', 'arts', 'tattoo', 'hats', 'barefoot', 'umbrella', 'floats', 'shepherd', 'skinny', 'forest', 'competing', 'having', 'jogging', 'puts', 'life', 'style', 'sideways', 'motorcyclists', 'cold', 'two', 'child', 'also', 'something', 'rocky', 'arcade', 'male', 'subway', 'dog', 'ski', 'star', 'speaking', 'computer', 'her', 'stare', 'corn', 'sandals', 'lifts', 'silver', 'robe', 'crying', 'bandanna', '

In [11]:
############### already done. Dont execute again please #######################
f = open("vocabulary.txt", "a+")
for i in range(len(vocab)):
    f.write(vocab[i])
    f.write("\n")
f.close()

In [12]:
file = open('flickr/Flickr8k_text/Flickr_8k.trainImages.txt')
doc = file.read()
train_images = list()
for word in doc.split('\n'):
    image_identifier = word.split('.')[0]
    train_images.append(image_identifier)
print(len(train_images))

6001


In [13]:
train_images

['2513260012_03d33305cf',
 '2903617548_d3e38d7f88',
 '3338291921_fe7ae0c8f8',
 '488416045_1c6d903fe0',
 '2644326817_8f45080b87',
 '218342358_1755a9cce1',
 '2501968935_02f2cd8079',
 '2699342860_5288e203ea',
 '2638369467_8fc251595b',
 '2926786902_815a99a154',
 '2851304910_b5721199bc',
 '3423802527_94bd2b23b0',
 '3356369156_074750c6cc',
 '2294598473_40637b5c04',
 '1191338263_a4fa073154',
 '2380765956_6313d8cae3',
 '3197891333_b1b0fd1702',
 '3119887967_271a097464',
 '2276499757_b44dc6f8ce',
 '2506892928_7e79bec613',
 '2187222896_c206d63396',
 '2826769554_85c90864c9',
 '3097196395_ec06075389',
 '3603116579_4a28a932e2',
 '3339263085_6db9fd0981',
 '2532262109_87429a2cae',
 '2076906555_c20dc082db',
 '2502007071_82a8c639cf',
 '3113769557_9edbb8275c',
 '3325974730_3ee192e4ff',
 '1655781989_b15ab4cbff',
 '1662261486_db967930de',
 '2410562803_56ec09f41c',
 '2469498117_b4543e1460',
 '69710415_5c2bfb1058',
 '3414734842_beb543f400',
 '3006217970_90b42e6b27',
 '2192411521_9c7e488c5e',
 '3535879138_928

In [14]:
train_descriptions = dict()
#train_descriptions_intermediate = list()
for line in str(descriptions).split('\n'):
    for image_id in descriptions:
        train_descriptions_intermediate = list()
        for i in range(len(descriptions[image_id])):
            train_descriptions_intermediate.append('start_sequence ' + ''.join(descriptions[image_id][i]) + ' end_sequence')
        train_descriptions[image_id] = train_descriptions_intermediate

In [15]:
train_descriptions

{'2156131463_5b53636cf0': ['start_sequence group of people are standing on beach near to white sunshade end_sequence',
  'start_sequence people in bathing suits are on beach looking at landform in the distance end_sequence',
  'start_sequence two men are watching others on beach shore end_sequence',
  'start_sequence two men in speedos on the beach end_sequence',
  'start_sequence two men stand looking at the ocean at tropical resort end_sequence'],
 '2675685200_0913d84d9b': ['start_sequence boy eating at table end_sequence',
  'start_sequence young boy in pajamas eats out of red bowl at wood table end_sequence',
  'start_sequence young boy making big mess on the floor and table while eating cereal end_sequence',
  'start_sequence young boy sits at table and eats as food is spilled all around end_sequence',
  'start_sequence the boy in blue and white pajamas is sitting at the table eating end_sequence'],
 '2436081047_bca044c1d3': ['start_sequence girl dismounts from swing as high as sh

In [16]:
############### already done. Dont execute again please #######################
f = open("descriptions.txt", "w+")
for key,value in train_descriptions.items():
    f.write(key)
    f.write("\t")
    f.write(str(value))
    f.write("\n")
f.close()

In [17]:
print(train_descriptions['3712923460_1b20ebb131'])
print(train_descriptions['2279980395_989d48ae72'])
print(len(train_descriptions))
#print(train_descriptions.keys())

['start_sequence bunch of people in camo pants run end_sequence', 'start_sequence group of men and woman wearing army pants and white shirt are running end_sequence', 'start_sequence group of men in camouflage pants and white tshirts are running in drill yard end_sequence', 'start_sequence group of people in army pants running end_sequence', 'start_sequence group of people wearing army clothes run together down the street end_sequence']
['start_sequence girl is buried under several playground balls end_sequence', 'start_sequence laughing baby is surrounded by balls of various colors end_sequence', 'start_sequence smiling child is surrounded by colored balls end_sequence', 'start_sequence little girl lying in many colored plastic balls end_sequence', 'start_sequence the child is covered with colorful balls end_sequence']
8092


In [18]:
############### already done. Dont execute again please #######################
model = InceptionV3(weights = 'imagenet')

W1101 06:39:03.093055 139829576251136 deprecation.py:237] From /usr/local/lib/python3.5/dist-packages/keras/backend/tensorflow_backend.py:4139: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W1101 06:39:22.694241 139829576251136 deprecation.py:506] From /usr/local/lib/python3.5/dist-packages/tensorflow/python/training/moving_averages.py:211: calling Zeros.__init__ (from tensorflow.python.ops.init_ops) with dtype is deprecated and will be removed in a future version.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [19]:
############### already done. Dont execute again please #######################

#model.add(Dense(2048))

model_new = Model(model.input, model.layers[-2].output)


In [20]:
############### already done. Dont execute again please #######################
model_new.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 299, 299, 3)  0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, 149, 149, 32) 864         input_1[0][0]                    
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, 149, 149, 32) 96          conv2d_1[0][0]                   
__________________________________________________________________________________________________
activation_1 (Activation)       (None, 149, 149, 32) 0           batch_normalization_1[0][0]      
__________________________________________________________________________________________________
conv2d_2 (

In [71]:
images = 'flickr/Flickr8k_Dataset/Flicker8k_Dataset'

img = glob.glob('flickr/Flickr8k_Dataset/Flicker8k_Dataset/*.jpg')


In [75]:
len(img)
img[0]

'flickr/Flickr8k_Dataset/Flicker8k_Dataset/3365783912_e12c3510d8.jpg'

In [20]:

train_images_file = 'flickr/Flickr8k_text/Flickr_8k.trainImages.txt'

train_images = set(open(train_images_file, 'r').read().strip().split('\n'))

#train_img = []

#for i in img: 
 #   if i in train_images:
  #      train_img.append(i)

In [21]:
print(len(train_images))
print(len(train_img))
train_images

6000
0


{'3465000218_c94e54e208.jpg',
 '2320125735_27fe729948.jpg',
 '3256456935_664a7a5bba.jpg',
 '2713554148_64cd465e71.jpg',
 '2773400732_5b65a25857.jpg',
 '2607383384_d9ce9de793.jpg',
 '688210930_85c5675d5b.jpg',
 '2076428547_738e0a132f.jpg',
 '3051125715_db76cebd1e.jpg',
 '1406010299_5755339f08.jpg',
 '3053916979_848d32261b.jpg',
 '302241178_a582c1b953.jpg',
 '2054308369_f9c6ec7815.jpg',
 '883040210_3c4a10f030.jpg',
 '3628994466_a12065d29b.jpg',
 '2414710960_a4cde4af60.jpg',
 '3710176138_fbfe00bd35.jpg',
 '374104006_7f32c8c5de.jpg',
 '55470226_52ff517151.jpg',
 '3337461409_e4e317853d.jpg',
 '2380464803_a64f05bfa9.jpg',
 '3261493263_381a4c5cc7.jpg',
 '2056041678_d6b5b39b26.jpg',
 '2192475933_d779bf42eb.jpg',
 '3601533527_6c2439113c.jpg',
 '2066241589_b80e9f676c.jpg',
 '3442138291_3e75f4bdb8.jpg',
 '3633396324_c4b24b1f51.jpg',
 '3556037801_3992ce6826.jpg',
 '3213622536_31da7f6682.jpg',
 '3488512097_e500cb499f.jpg',
 '2661567396_cbe4c2e5be.jpg',
 '3183195653_11b66acb34.jpg',
 '3004359992_f6b

In [22]:
test_images_file = 'flickr/Flickr8k_text/Flickr_8k.testImages.txt'

test_images = set(open(test_images_file, 'r').read().strip().split('\n'))

#test_img = []

#for i in img:
 #   if i[len(images):] in test_images:
  #      test_img.append(i)

In [24]:
#len(test_img)

In [86]:
############### already done. Dont execute again please #######################
#path = glob.glob('Flicker8k_Dataset/*.jpg')
#images = list()
#count = 0
def preprocess(image_path):    
    img = image.load_img('flickr/Flickr8k_Dataset/Flicker8k_Dataset/' + image_path)#, target_size=(299, 299))
    #n = cv2.imread(image_path)
    x = image.img_to_array(img)
    x = np.resize(x, (299, 299, 3))
    x = np.expand_dims(x, axis = 0)
    #y = preprocess_input(x)
    return x

In [87]:
############### already done. Dont execute again please #######################
def image_to_vector(img):
    img = preprocess(img)
    #print(img.shape)
    x = model_new.predict(img)
    feature_vector_2048 = np.reshape(x, x.shape[1])
    return feature_vector_2048 

In [112]:
fea_vec_2048 = {}
count = 0
for img in train_images:
    if count in range(0, 3000):
        fea_vec_2048[img] = image_to_vector(img)
        count += 1
    else:
        break

In [113]:
############### already done. Dont execute again please #######################
fea_vec_20481 = {}
count = 0
for img in train_images:
    if count in range(3000, 6000):
        fea_vec_20481[img] = image_to_vector(img)
        count += 1
    else:
        count += 1
    

In [114]:
dest_dict = dict(list(fea_vec_2048.items()) + list(fea_vec_20481.items()))

In [64]:
len(dest_dict)

NameError: name 'dest_dict' is not defined

In [116]:
############### already done. Dont execute again please #######################
with open("encoded_train_images.pkl", "wb") as encoded_pickle:
    pickle.dump(dest_dict, encoded_pickle)

In [73]:
encoded_train_images = {}
with open("encoded_train_images.pkl",'rb') as rfp: 
    while 1:
        try:
            encoded_train_images.update(pickle.load(rfp))
        except EOFError:
            break

In [118]:
encoded_train_images.size

AttributeError: 'list' object has no attribute 'size'

In [20]:
dest_dict

NameError: name 'dest_dict' is not defined

In [ ]:
"""
encoded_img ={}
for i in range(len(train_images)):
    #print(i)
    encoded_img[train_images[i]] = encoded_train_images[2048 * i: (2048 * i) + 2048 ]
"""

In [36]:
encoded_img['1191338263_a4fa073154']
#len(encoded_img)

NameError: name 'encoded_img' is not defined

In [26]:
f = open("flickr/Flickr8k_Dataset/vocabulary1.txt", "r")
if f.mode == "r":
    vocabfromfile = f.readlines()
print(len(vocabfromfile))
f.close()

1839


In [27]:
ixtoword = {}
wordtoix = {}

ix = 1
for w in vocabfromfile:
    wordtoix[w] = ix
    ixtoword[ix] = w
    ix += 1

In [28]:
print(ix)
print(len(ixtoword))
vocab_size = len(ixtoword) + 1

1840
1839


In [29]:
f = open("descriptions.txt", "r")
if f.mode == "r":
    descriptions = f.readlines()
print(len(descriptions))
f.close()


8092


In [30]:
def to_lines(descriptions):
    all_desc = list()
    for key in descriptions.keys():
        [all_desc.append(d) for d in descriptions[key]]
    return all_desc

# calculate the length of the description with the most words
def max_length(descriptions):
    lines = to_lines(descriptions)
    return max(len(d.split()) for d in lines)

# determine the maximum sequence length
max_length = max_length(train_descriptions)
print('Description Length: %d' % max_length)

Description Length: 34


In [95]:
# data generator, intended to be used in a call to model.fit_generator()
def data_generator(descriptions, photos, wordtoix, max_length, num_photos_per_batch):
    X1, X2, y = list(), list(), list()
    n=0
    # loop for ever over images
    while 1:
        for key, value in photos.items():
            n+=1
            #key1 = str(key) + '.jpg'
            #print(key1)
            photo = value
            #print(key1)
            #photo = [ sub[key1] for sub in photos ]
            #print(photo)
            key1  = str(key).split('.')[0]
            if key1 in descriptions.keys():
                
                desc_list = descriptions[key1]
                for desc in desc_list:
                
                    seq = [wordtoix[word] for word in desc.split(' ') if word in wordtoix]
                
                    for i in range(1, len(seq)):
                    
                        in_seq, out_seq = seq[:i], seq[i]
                    
                        in_seq = pad_sequences([in_seq], maxlen=max_length)[0]
                    
                        out_seq = to_categorical([out_seq], num_classes=vocab_size)[0]
                    
                        X1.append(photo)
                        X2.append(in_seq)
                        y.append(out_seq)
            
                if n==num_photos_per_batch:
                    #yield [[np.array(X1), np.array(X2)], np.array(y)]
                    X1, X2, y = list(), list(), list()
                    n=0

In [71]:
if '2675685200_0913d84d9b.jpg' in encoded_train_images:
    print(1)
else:
    print(0)

0


In [86]:
print(len(encoded_train_images))
print(len(train_descriptions))

6000
8092


In [32]:
def get_value(listOfDicts, key):
    for subVal in listOfDicts:
        if key in subVal:
            return subVal[key]

In [33]:
def get_key(listOfDicts, key):
    for subVal in listOfDicts:
        if key in subVal:
            return key

In [34]:
dest_dect = Convert(encoded_train_images)

NameError: name 'Convert' is not defined

In [83]:

for keys in train_descriptions.items():
    keys1 = str(keys) + '.jpg'
    print(keys1)
    if keys1 not in str(encoded_train_images.keys()):
        print(keys1)
        count += 1

('2156131463_5b53636cf0', ['start_sequence group of people are standing on beach near to white sunshade end_sequence', 'start_sequence people in bathing suits are on beach looking at landform in the distance end_sequence', 'start_sequence two men are watching others on beach shore end_sequence', 'start_sequence two men in speedos on the beach end_sequence', 'start_sequence two men stand looking at the ocean at tropical resort end_sequence']).jpg
('2675685200_0913d84d9b', ['start_sequence boy eating at table end_sequence', 'start_sequence young boy in pajamas eats out of red bowl at wood table end_sequence', 'start_sequence young boy making big mess on the floor and table while eating cereal end_sequence', 'start_sequence young boy sits at table and eats as food is spilled all around end_sequence', 'start_sequence the boy in blue and white pajamas is sitting at the table eating end_sequence']).jpg
('2436081047_bca044c1d3', ['start_sequence girl dismounts from swing as high as she can an

('3208999896_dab42dc40b', ['start_sequence bride groom guys and women end_sequence', 'start_sequence bride and groom are the center of this picture with three bridesmaids in red dresses to the left and groomsmen to the right end_sequence', 'start_sequence couple taking wedding photo with their wedding party end_sequence', 'start_sequence formal wedding party poses smiling for wedding photo in church end_sequence', 'start_sequence the wedding party is posing for picture in front of the church alter end_sequence']).jpg
('1991806812_065f747689', ['start_sequence boxer punches boxer in the face end_sequence', 'start_sequence fighter attempts to kick another fighter while the other fighter blocks his kick end_sequence', 'start_sequence kickboxer jumping for kick end_sequence', 'start_sequence two boxers are in the ring end_sequence', 'start_sequence two men kickbox in ring one man punching the other end_sequence']).jpg
('1303727066_23d0f6ed43', ['start_sequence dark haired bearded man weari

('3184206563_5435f2b494', ['start_sequence woman in blue shirt runs through field of dry grass end_sequence', 'start_sequence woman in the blue sweater is running through brown field end_sequence', 'start_sequence woman jogging on an open field end_sequence', 'start_sequence woman runs outside in blue coat end_sequence', 'start_sequence the woman in the blue jacket ran through the field end_sequence']).jpg
('478592803_f57cc9c461', ['start_sequence the backs of two asian girls wearing red tops and holding red flags end_sequence', 'start_sequence two asian girls dressed in red are standing at busy pedestrian crossing end_sequence', 'start_sequence two girls in red jackets are trying to cross traffic with lot of cars going by end_sequence', 'start_sequence two people in red jackets with red sashes standing on street corner end_sequence', 'start_sequence two women attempting to cross busy street in china end_sequence']).jpg
('3606093421_eddd46c2c7', ['start_sequence the orange rescue boat 

('3605061440_1d08c80a57', ['start_sequence children one with stick and six petting dog with blue leash end_sequence', 'start_sequence group of children are petting white dog on the grass end_sequence', 'start_sequence group of children gather around white dog on the grass outside end_sequence', 'start_sequence group of children playing with dog end_sequence', 'start_sequence group of children surround and pet white dog with blue collar on grass end_sequence']).jpg
('2701042060_92508ea8fa', ['start_sequence black dog is drinking next to brown and white dog that is looking at an orange ball in the lake whilst horse and rider passes behind end_sequence', 'start_sequence brown and white dog and black dog near water with man on horseback in the background end_sequence', 'start_sequence dogs in the water with basketball and person on horseback end_sequence', 'start_sequence two dogs are playing near water next to deflated basketball end_sequence', 'start_sequence two dogs stand on sand surro

('3426144752_28d63615ca', ['start_sequence little girl plays with plane end_sequence', 'start_sequence young blonde boy holding toy airplane end_sequence', 'start_sequence young blonde child holding an airplane end_sequence', 'start_sequence the blonde haired child is holding the small plane end_sequence', 'start_sequence the blond haired and blue eyed child holds the wooden airplane in his hands end_sequence']).jpg
('3669069522_555c97fbfb', ['start_sequence one woman and two men on bench end_sequence', 'start_sequence one woman holding flowers and two men on bench end_sequence', 'start_sequence three middle aged people sitting on park bench with rock wall in the background end_sequence', 'start_sequence three people sit on bench outside end_sequence', 'start_sequence two men and woman sitting on bench end_sequence']).jpg
('466176275_f40d37851e', ['start_sequence grey labradoodle jumps over another large dog end_sequence', 'start_sequence one grey puddle jumping in the air in front of 

...

('1105959054_9c3a738096', ['start_sequence child painting picture end_sequence', 'start_sequence an artist paints clouds onto canvas end_sequence', 'start_sequence young girl painting picture end_sequence', 'start_sequence young girl with braids is painting with water colors on white paper on the wall end_sequence', 'start_sequence the child paints on large paper with water colors end_sequence']).jpg
('2599131872_65789d86d5', ['start_sequence two blond girls are playing together end_sequence', 'start_sequence two girls enjoy themselves whilst wind blows through their hair end_sequence', 'start_sequence two girls with long hair jumping on trampoline end_sequence', 'start_sequence two little blonde girls twirl their hair end_sequence', 'start_sequence two little girls are playing on trampoline end_sequence']).jpg
('2720985888_8f5920e8cf', ['start_sequence little girl laughs while playing in play house end_sequence', 'start_sequence little girl with ponytails laughs near plastic castle pl

('1287073593_f3d2a62455', ['start_sequence group of dogs pull person on dog sled up hill end_sequence', 'start_sequence dogsled rider pulled past flags on snowy hill end_sequence', 'start_sequence dogs pulling sled in sled race end_sequence', 'start_sequence five sled dogs are pulling person on sled through the snow end_sequence', 'start_sequence the man is mushing his dogs on snow trail end_sequence']).jpg
('2405599120_ec5f32af6f', ['start_sequence baby is sitting on the floor surrounded by diapers and basket end_sequence', 'start_sequence baby on floor with an overturned basket and articles on the floor end_sequence', 'start_sequence baby plays near an overturned basket of diapers end_sequence', 'start_sequence toddler sits with diapers spread around the floor end_sequence', 'start_sequence young baby sitting in the middle of the floor surrounded by clean diapers end_sequence']).jpg
('3516267455_ca17cc1323', ['start_sequence dog in lake end_sequence', 'start_sequence dog running into

('535309053_ec737abde8', ['start_sequence campsite has been established amidst the trees and bushes end_sequence', 'start_sequence campsite with tents and picnic tables end_sequence', 'start_sequence group of people camp in tents near some trees end_sequence', 'start_sequence woman at campground end_sequence', 'start_sequence people are camping in group end_sequence']).jpg
('536828916_b763b82949', ['start_sequence curly redheaded girl with large headband in her hair end_sequence', 'start_sequence girl with long curly red hair and green eyes end_sequence', 'start_sequence redhaired woman looks offcamera end_sequence', 'start_sequence red haired woman looks past the cameraman end_sequence', 'start_sequence the redheaded woman is staring off into the distance end_sequence']).jpg
('578274277_652cae32ba', ['start_sequence boy has his swear gear on end_sequence', 'start_sequence boy with floatlys gets ready to jump in the pool end_sequence', 'start_sequence young boy wearing red floaties abo

('3363836972_c87b58c948', ['start_sequence soccer player kicking goal in end_sequence', 'start_sequence soccer player kicks ball into the unmanned goal end_sequence', 'start_sequence soccer player prepares to kick the ball end_sequence', 'start_sequence man in red white and blue sport uniform on field with soccer ball above ground in front of him end_sequence', 'start_sequence view of soccer ball being kicked into goal net end_sequence']).jpg
('2944193661_7b255af9cc', ['start_sequence man asleep on yellow striped bench with his feet on baggage cart end_sequence', 'start_sequence man in sweatshirt and blue jeans is taking nap on bench end_sequence', 'start_sequence man in jeans resting on striped bench with his feet on luggage cart end_sequence', 'start_sequence man is asleep on bench in the subway end_sequence', 'start_sequence man sleeping on bench in subway station end_sequence']).jpg
('1224851143_33bcdd299c', ['start_sequence boy eats with spoon end_sequence', 'start_sequence little

('3088322308_b0c940b3a3', ['start_sequence group of people at distance on beach end_sequence', 'start_sequence man woman and two girls walk on the beach barefoot end_sequence', 'start_sequence four people are walking on beach end_sequence', 'start_sequence people walking in the water along the beach end_sequence', 'start_sequence this family is walking on the beach end_sequence']).jpg
('2540326842_bb26cec999', ['start_sequence group of kids look out of fence end_sequence', 'start_sequence group of kids stares through fence at some type of animal end_sequence', 'start_sequence children look through fence end_sequence', 'start_sequence five children and two adults standing side by side looking at animals in cage end_sequence', 'start_sequence several children lined up at and looking through fence end_sequence']).jpg
('3703413486_3c682732a0', ['start_sequence boy sticks an aligator puppet out of camper van window end_sequence', 'start_sequence two boys looking out the window of an rv end_

In [35]:
type(encoded_train_images)
encoded_train_images
#encoded_train_images['2215165918_2bf5b659dd.jpg']
#train_descriptions.keys()


[{'3084010872_cbc3ea8239.jpg': array([0.2786224 , 0.05346941, 0.0407874 , ..., 0.        , 0.5881108 ,
         0.09009294], dtype=float32),
  '3465000218_c94e54e208.jpg': array([0.        , 0.01228085, 0.13823198, ..., 0.        , 0.        ,
         0.        ], dtype=float32),
  '3256456935_664a7a5bba.jpg': array([0.        , 0.22027421, 0.        , ..., 0.        , 0.        ,
         0.        ], dtype=float32),
  '2773400732_5b65a25857.jpg': array([0.44729197, 0.        , 0.31648642, ..., 0.        , 0.00463686,
         0.48629385], dtype=float32),
  '2998185688_8d33e4ce38.jpg': array([0.        , 2.1726627 , 0.5627474 , ..., 0.        , 0.        ,
         0.16788441], dtype=float32),
  '3461106572_920c8c0112.jpg': array([5.1837645 , 0.1635404 , 2.085631  , ..., 0.03782899, 0.        ,
         7.256114  ], dtype=float32),
  '2607383384_d9ce9de793.jpg': array([0.        , 0.        , 0.        , ..., 0.        , 0.        ,
         0.07207187], dtype=float32),
  '688210930_

In [36]:
######################### already done this. dont do this again please ################
#glove_dir = 'glove.6B'
embeddings_index = {} # empty dictionary
f = open('glove.6B/glove.6B.200d.txt', encoding="utf-8")

for line in f:
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()
print('Found %s word vectors.' % len(embeddings_index))

Found 400000 word vectors.


In [37]:
embedding_dim = 200

# Get 200-dim dense vector for each of the 10000 words in out vocabulary
embedding_matrix = np.zeros((vocab_size, embedding_dim))

for word, i in wordtoix.items():
    #if i < max_words:
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # Words not found in the embedding index will be all zeros
        embedding_matrix[i] = embedding_vector

In [38]:
embedding_matrix.shape

(1840, 200)

In [39]:
############ lstm model #########################3

inputs1 = Input(shape=(4096,))
fe1 = Dropout(0.5)(inputs1)
fe2 = Dense(256, activation='relu')(fe1)
inputs2 = Input(shape=(max_length,))
se1 = Embedding(vocab_size, embedding_dim, mask_zero=True)(inputs2)
se2 = Dropout(0.5)(se1)
se3 = LSTM(256)(se2)
decoder1 = add([fe2, se3])
decoder2 = Dense(256, activation='relu')(decoder1)
outputs = Dense(vocab_size, activation='softmax')(decoder2)
model = Model(inputs=[inputs1, inputs2], outputs=outputs)

W1101 06:41:36.899569 139829576251136 deprecation.py:506] From /usr/local/lib/python3.5/dist-packages/keras/backend/tensorflow_backend.py:3445: calling dropout (from tensorflow.python.ops.nn_ops) with keep_prob is deprecated and will be removed in a future version.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [40]:
model.layers[2].set_weights([embedding_matrix])
model.layers[2].trainable = False

In [41]:
model.compile(loss='categorical_crossentropy', optimizer='adam')

W1101 06:41:39.157496 139829576251136 deprecation.py:237] From /usr/local/lib/python3.5/dist-packages/keras/backend/tensorflow_backend.py:3295: The name tf.log is deprecated. Please use tf.math.log instead.



In [42]:
model.optimizer.learning_rate = 0.0001
epochs = 10
number_pics_per_batch = 6
steps = len(train_descriptions)//number_pics_per_batch

In [96]:
for i in range(epochs):
    generator = data_generator(train_descriptions, encoded_train_images, wordtoix, max_length, number_pics_per_batch)
    model.fit_generator(generator, epochs=1, steps_per_epoch=steps, verbose=1)

KeyboardInterrupt: 

In [45]:
model.save("flickr/Flicker8k_Datset/model1.h5")

OSError: Unable to create file (unable to open file: name = 'flickr/Flicker8k_Datset/model1.h5', errno = 2, error message = 'No such file or directory', flags = 13, o_flags = 242)